# Pesquisa CBGG 2025

## Import de bibliotecas

In [1]:
from pysus import SIH
from pysus.ftp import FTPSingleton
import pandas as pd
import source.graphfile as gf

## Download e carregamento dos Dados

In [2]:
FTPSingleton.timeout = 180
print("Carregando arquivos do SIH...")
sih = SIH().load()
print("Arquivos do SIH carregados!")

files = sih.get_files("RD", uf="CE",
year=[2014,2015,2016,2017,2018,2019,2020,2021,2022,2023],
month=[1,2,3,4,5,6,7,8,9,10,11,12])

print("Baixando arquivos do SIH...")
arquivos = sih.download(files,local_dir="./dados/DBC")
print("Arquivos do SIH baixados!")
print("Gerando dataframe dos dados do SIH...")
dataframes = []
for arquivo in arquivos:
    df = arquivo.to_dataframe()
    dataframes.append(df)
    print(f"df {arquivo} gerado!")
df_sih = pd.concat(dataframes, ignore_index=True)
df_sih.to_csv("dados/dados_sih.csv")
print("Datafrane do SIH gerado!")


Carregando arquivos do SIH...
Arquivos do SIH carregados!
Baixando arquivos do SIH...


3259775it [00:00, 273992251.09it/s]    

Arquivos do SIH baixados!
Gerando dataframe dos dados do SIH...


df dados/DBC/RDCE1401.parquet gerado!
df dados/DBC/RDCE1402.parquet gerado!
df dados/DBC/RDCE1403.parquet gerado!
df dados/DBC/RDCE1404.parquet gerado!
df dados/DBC/RDCE1405.parquet gerado!
df dados/DBC/RDCE1406.parquet gerado!
df dados/DBC/RDCE1407.parquet gerado!
df dados/DBC/RDCE1408.parquet gerado!
df dados/DBC/RDCE1409.parquet gerado!
df dados/DBC/RDCE1410.parquet gerado!
df dados/DBC/RDCE1411.parquet gerado!
df dados/DBC/RDCE1412.parquet gerado!
df dados/DBC/RDCE1501.parquet gerado!
df dados/DBC/RDCE1502.parquet gerado!
df dados/DBC/RDCE1503.parquet gerado!
df dados/DBC/RDCE1504.parquet gerado!
df dados/DBC/RDCE1505.parquet gerado!
df dados/DBC/RDCE1506.parquet gerado!
df dados/DBC/RDCE1507.parquet gerado!
df dados/DBC/RDCE1508.parquet gerado!
df dados/DBC/RDCE1509.parquet gerado!
df dados/DBC/RDCE1510.parquet gerado!
df dados/DBC/RDCE1511.parquet gerado!
df dados/DBC/RDCE1512.parquet gerado!
df dados/DBC/RDCE1601.parquet gerado!
df dados/DBC/RDCE1602.parquet gerado!
df dados/DBC

In [3]:
cnes_mapping = pd.read_csv("dados/CNESBR.csv")
munic_mapping = pd.read_csv("dados/MUNICSBR.csv")
df = pd.read_csv("dados/dados_sih.csv")

# Garantir que os códigos estão no mesmo formato (string)
df["CNES"] = df["CNES"].astype(str)
df["MUNIC_RES"] = df["MUNIC_RES"].astype(str)
cnes_mapping["CNES"] = cnes_mapping["CNES"].astype(str)
munic_mapping["COD"] = munic_mapping["COD"].astype(str)

# Substituir os códigos de CNES pelos nomes
df = df.merge(cnes_mapping.rename(columns={"NOMEFANT": "HOSPITAL"}), how="left", on="CNES")

# Substituir os códigos de MUNIC_RES pelos nomes
df = df.merge(munic_mapping.rename(columns={"MUNIC": "MUNICIPIO", "COD": "MUNIC_RES"}), how="left", on="MUNIC_RES")

# Exibir algumas linhas para verificar
print(df.head())

/tmp/ipykernel_40749/979251331.py:3: DtypeWarning: Columns (42,78,79,88,89,96,97,98,99,100,101,102) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("dados/dados_sih.csv")


   Unnamed: 0   UF_ZI  ANO_CMPT  MES_CMPT  ESPEC  CGC_HOSP          N_AIH  \
0           0  230730      2014         1      2       NaN  2314101066079   
1           1  230730      2014         1      7       NaN  2314101064209   
2           2  230730      2014         1      7       NaN  2314101066630   
3           3  230730      2014         1      7       NaN  2314101066640   
4           4  230730      2014         1      7       NaN  2314101066651   

   IDENT       CEP MUNIC_RES  ...  TPDISEC2  TPDISEC3  TPDISEC4  TPDISEC5  \
0      1  63010970    230730  ...       NaN       NaN       NaN       NaN   
1      1  63051170    230730  ...       NaN       NaN       NaN       NaN   
2      1  63031185    230730  ...       NaN       NaN       NaN       NaN   
3      1  63050216    230730  ...       NaN       NaN       NaN       NaN   
4      1  63040810    230730  ...       NaN       NaN       NaN       NaN   

   TPDISEC6  TPDISEC7  TPDISEC8  TPDISEC9                        HOSPITAL 

## Filtro dos Dados

In [4]:
def calcular_idade_convertida(row):
    if row['COD_IDADE'] == 5:  # Idade maior ou igual a 100 anos
        return 100 + row['IDADE']
    elif row['COD_IDADE'] == 2:  # Idade em dias
        return row['IDADE'] // 365  # Aproximar para anos
    elif row['COD_IDADE'] == 3:  # Idade em meses
        return row['IDADE'] // 12  # Aproximar para anos
    elif row['COD_IDADE'] == 4:  # Idade em anos
        return row['IDADE']
    else:
        return None  # Caso COD_IDADE seja inválido

# Criar a nova coluna 'idade_convertida'
df['idade_convertida'] = df.apply(calcular_idade_convertida, axis=1)

In [5]:
df["IDADE"] = pd.to_numeric(df["IDADE"], errors="coerce")
df_s72 = df[
    df["DIAG_PRINC"].isin(["S720", "S721", "S722"]) & 
    (df["idade_convertida"] >= 60)
]
df_s72 = df_s72.dropna(subset=["HOSPITAL", "MUNICIPIO"])

# Carregar o arquivo TB_SIGTAW.csv que contém os códigos e nomes dos procedimentos
tb_sig = pd.read_csv("dados/TB_SIGTAW.csv")

# Renomear as colunas de TB_SIGTAW.csv para facilitar o merge
tb_sig.rename(columns={"IP_COD": "PROC_REA", "IP_DSCR": "PROCEDIMENTO"}, inplace=True)

# Garantir que os tipos de dados sejam consistentes para o merge (caso necessário)
df_s72["PROC_REA"] = df_s72["PROC_REA"].astype(str)
tb_sig["PROC_REA"] = tb_sig["PROC_REA"].astype(str)

# Realizar o merge para adicionar a coluna 'PROCEDIMENTO'
df_s72 = df_s72.merge(tb_sig, on="PROC_REA", how="left")
print("AIHs total do CE: ",len(df_s72))

AIHs total do CE:  12589


In [6]:
df["IDADE"] = pd.to_numeric(df["IDADE"], errors="coerce")
# TODO: Levantar a diferença dos dados de Municipios Fora e Dentro do Estado do Ceará
df_s72_ce = df[
    df["DIAG_PRINC"].isin(["S720", "S721", "S722"]) & 
    df["MUNICIPIO"].str.endswith(", CE") & 
    (df["idade_convertida"] >= 60)
]
df_s72_ce = df_s72_ce.dropna(subset=["HOSPITAL", "MUNICIPIO"])

# Carregar o arquivo TB_SIGTAW.csv que contém os códigos e nomes dos procedimentos
tb_sig = pd.read_csv("dados/TB_SIGTAW.csv")

# Renomear as colunas de TB_SIGTAW.csv para facilitar o merge
tb_sig.rename(columns={"IP_COD": "PROC_REA", "IP_DSCR": "PROCEDIMENTO"}, inplace=True)

# Garantir que os tipos de dados sejam consistentes para o merge (caso necessário)
df_s72_ce["PROC_REA"] = df_s72_ce["PROC_REA"].astype(str)
tb_sig["PROC_REA"] = tb_sig["PROC_REA"].astype(str)

# Realizar o merge para adicionar a coluna 'PROCEDIMENTO'
df_s72_ce = df_s72_ce.merge(tb_sig, on="PROC_REA", how="left")
print("AIHs apenas de municipios do CE: ", len(df_s72_ce))

AIHs apenas de municipios do CE:  12527


## Plotar Grafo

In [61]:
# Carregar os dados geográficos
geo_data = pd.read_csv("./dados/geograf.csv")
grafoS72 = gf.criar_grafo(geo_data, df_s72)
gf.plotar_grafo_folium(grafoS72,output_path='./output/grafoS72.html')

## Gerar caracterização dos dados

### Tabela de caracterização

In [8]:
# Raça (ordenado crescentemente pela categoria)
raca = (df_s72["RACA_COR"].value_counts(normalize=True) * 100).round(1).reset_index()
raca.columns = ["Raça", "Percentual (%)"]
raca = raca.sort_values(by="Raça")  # Ordenar pela coluna "Raça"

# Sexo (ordenado crescentemente por categoria)
sexo = (df_s72["SEXO"].value_counts(normalize=True) * 100).round(1).reset_index()
sexo.columns = ["Sexo", "Percentual (%)"]
sexo = sexo.sort_values(by="Sexo")  # Ordenar pela coluna "Sexo"

# Estatísticas de Idade (não precisa de ordenação, apenas exibição)
idade_stats = pd.DataFrame({
    "Estatística": ["Mínima", "Máxima", "Média", "Mediana", "Moda"],
    "Idade": [
        int(df_s72["idade_convertida"].min()),
        int(df_s72["idade_convertida"].max()),
        round(df_s72["idade_convertida"].mean(), 1),
        int(df_s72["idade_convertida"].median()),
        int(df_s72["idade_convertida"].mode()[0])
    ]
})

# Faixa Etária (<60, 60-69, 70-79, 80-89, 90-99, 100+)
bins = [0, 59, 69, 79, 89, 99, float("inf")]
labels = ["<60", "60-69", "70-79", "80-89", "90-99", "100+"]
df_s72["FAIXA_ETÁRIA"] = pd.cut(df_s72["idade_convertida"], bins=bins, labels=labels, ordered=True)
faixa_etaria = (df_s72["FAIXA_ETÁRIA"].value_counts(normalize=True) * 100).round(1).reset_index()
faixa_etaria.columns = ["Faixa Etária", "Percentual (%)"]
faixa_etaria = faixa_etaria.sort_values(by="Faixa Etária")  # Ordenar pela coluna "Faixa Etária"

# Exibir as tabelas organizadas
print("Tabela de Raça:")
print(raca)

print("\nTabela de Sexo:")
print(sexo)

print("\nEstatísticas de Idade:")
print(idade_stats)

print("\nTabela de Faixa Etária:")
print(faixa_etaria)

Tabela de Raça:
   Raça  Percentual (%)
2     1             6.9
4     2             1.0
0     3            64.2
3     4             4.4
5     5             0.0
1    99            23.5

Tabela de Sexo:
   Sexo  Percentual (%)
1     1            26.4
0     3            73.6

Estatísticas de Idade:
  Estatística  Idade
0      Mínima   60.0
1      Máxima  113.0
2       Média   79.2
3     Mediana   80.0
4        Moda   82.0

Tabela de Faixa Etária:
  Faixa Etária  Percentual (%)
5          <60             0.0
2        60-69            16.4
1        70-79            32.7
0        80-89            38.6
3        90-99            11.8
4         100+             0.5


### Frequencia de procedimentos

In [9]:
frequencia_procedimento = df_s72["PROCEDIMENTO"].value_counts()
percentual_procedimento = df_s72["PROCEDIMENTO"].value_counts(normalize=True) * 100

# Criar o DataFrame com as frequências e percentuais
tabela_frequencias_procedimentos = pd.DataFrame({
    'Frequência': frequencia_procedimento,
    'Percentual (%)': percentual_procedimento
}).reset_index()

# Renomear a coluna para "PROCEDIMENTO"
tabela_frequencias_procedimentos.rename(columns={'index': 'PROCEDIMENTO'}, inplace=True)

# Adicionar os códigos dos procedimentos (PROC_REA)
tabela_frequencias_procedimentos = tabela_frequencias_procedimentos.merge(
    tb_sig[['PROC_REA', 'PROCEDIMENTO']],
    on='PROCEDIMENTO',
    how='left'
)

# Reordenar colunas para melhor visualização
tabela_frequencias_procedimentos = tabela_frequencias_procedimentos[['PROC_REA', 'PROCEDIMENTO', 'Frequência', 'Percentual (%)']]

tabela_frequencias_procedimentos.to_excel("output/freq_procedimentos.xlsx")
print(tabela_frequencias_procedimentos)

     PROC_REA                                       PROCEDIMENTO  Frequência  \
0   408050632  TRATAMENTO CIRURGICO DE FRATURA TRANSTROCANTER...        5084   
1   408040050                    ARTROPLASTIA PARCIAL DE QUADRIL        1521   
2   408050616   TRATAMENTO CIRURGICO DE FRATURA SUBTROCANTERIANA        1398   
3   408040092  ARTROPLASTIA TOTAL PRIMARIA DO QUADRIL NAO CIM...         950   
4   408050489  TRATAMENTO CIRURGICO DE FRATURA / LESAO FISARI...         789   
5   415010012                  TRATAMENTO C/ CIRURGIAS MULTIPLAS         734   
6   408040084   ARTROPLASTIA TOTAL PRIMARIA DO QUADRIL CIMENTADA         636   
7   308010019  TRATAMENTO CLINICO/CONSERVADOR DE TRAUMATISMOS...         504   
8   415030013           TRATAMENTO CIRURGICO EM POLITRAUMATIZADO         290   
9   303090138  TRATAMENTO CONSERVADOR DE FRATURA / LESAO LIGA...         272   
10  301060070  DIAGNOSTICO E/OU ATENDIMENTO DE URGENCIA EM CL...         144   
11  301060088  DIAGNOSTICO E/OU ATENDIME

### Frequencia de idade

In [10]:
frequencia_idade = df_s72["idade_convertida"].value_counts()
percentual_idade = df_s72["idade_convertida"].value_counts(normalize=True) * 100

tabela_frequencias_idades = pd.DataFrame({
    'Frequência': frequencia_idade,
    'Percentual (%)': percentual_idade
})

tabela_frequencias_idades.to_excel("output/freq_idades.xlsx")
print(tabela_frequencias_idades)

                  Frequência  Percentual (%)
idade_convertida                            
82                       569        4.519819
81                       548        4.353007
83                       534        4.241798
79                       520        4.130590
84                       513        4.074986
80                       513        4.074986
85                       513        4.074986
78                       488        3.876400
77                       468        3.717531
86                       463        3.677814
87                       459        3.646040
76                       443        3.518945
75                       429        3.407737
88                       421        3.344189
73                       403        3.201207
74                       402        3.193264
72                       349        2.772261
89                       330        2.621336
71                       315        2.502184
70                       301        2.390976
91        

### Rede Geral

In [62]:
# Lista de valores a serem removidos da coluna 'PROC_REA'
filtro_cirurgia = ['408040050','408040084','408040092',
                   '408050489','408050616',
                   '408050632','408060069',
                   '415010012']
filtro_procedimentos_paliativos = ['403020077','403050030','408050233','408060123','408060158']
filtro_tratamento_conservador= ['303090138','308010019']
filtro_geral = filtro_cirurgia + filtro_procedimentos_paliativos + filtro_tratamento_conservador

df_rede_geral = df_s72[df_s72['PROC_REA'].isin(filtro_geral)]
df_rede_cirurgia = df_s72[df_s72['PROC_REA'].isin(filtro_cirurgia)]
df_rede_procedimentos_paliativos = df_s72[df_s72['PROC_REA'].isin(filtro_procedimentos_paliativos)]
df_rede_tratamento_conservador = df_s72[df_s72['PROC_REA'].isin(filtro_tratamento_conservador)]

print("Quantiade de AIHs Rede Procedimentos Paliativos: ",len(df_rede_procedimentos_paliativos))
print("Quantiade de AIHs Rede Tratamento Clínico Conservador: ",len(df_rede_tratamento_conservador))
print("Quantiade de AIHs Rede Cirurgica: ",len(df_rede_cirurgia))
print("Quantiade de AIHs Rede Geral: ",len(df_rede_geral))

Quantiade de AIHs Rede Procedimentos Paliativos:  12
Quantiade de AIHs Rede Tratamento Clínico Conservador:  776
Quantiade de AIHs Rede Cirurgica:  11116
Quantiade de AIHs Rede Geral:  11904


In [63]:
tb_cnes = pd.read_csv("dados/CNESBR.csv")
tb_cnes.rename(columns={"NOMEFANT": "HOSPITAL"}, inplace=True)
tb_cnes

CNES                                 HOSPITAL
0          27               CASA DE SAUDE SANTA HELENA
1          35                   HOSPITAL MENDO SAMPAIO
2          94   MATERNIDADE PADRE GERALDO LEITE BASTOS
3         396                    HOSPITAL DAS CLINICAS
4         418              HOSPITAL AGAMENON MAGALHAES
...       ...                                      ...
6883  9922970                     HOSPITAL SAO GABRIEL
6884  9923837  HOSPITAL DA MULHER DRA NISE DA SILVEIRA
6885  9950931                 HOSPITAL DIA SANTO AMARO
6886  9994289   POLICLINICA MUNICIPAL ESTEFANIA FARIAS
6887  9997784     HOSPITAL E MATERNIDADE NAILA GONCALO

[6888 rows x 2 columns]

In [64]:
tab_municipio = pd.read_csv("dados/MUNICSBR.csv")
tab_municipio.rename(columns={"COD": "MUNIC_RES","MUNIC": "MUNICIPIO"}, inplace=True)
tab_municipio

MUNIC_RES                                 MUNICIPIO
0        261080                                 PEDRA, PE
1        314890                       PEDRA DO INDAIA, MG
2        240950                          PEDRA GRANDE, RN
3        314910                              PEDRALVA, MG
4        292410                                PEDRAO, BA
...         ...                                       ...
5715     241150                         SANTO ANTONIO, RN
5716     354800                SANTO ANTONIO DE POSSE, SP
5717     539938  REGIAO ADMINISTRATIVA DA ARNIQUEIRAS, DF
5718     539940      REGIAO ADMINISTRATIVA DA ASA SUL, DF
5719     539939    REGIAO ADMINISTRATIVA DA ASA NORTE, DF

[5720 rows x 2 columns]

In [65]:
pd.set_option('display.max_rows', 200)

In [66]:
def calcularFrequenciaCNES(df, output="output/freq_CNES.xlsx"):
    frequencia_cnes = df["CNES"].value_counts()
    percentual_cnes = df["CNES"].value_counts(normalize=True) * 100

    # Criar o DataFrame com as frequências e percentuais
    tabela_frequencias_cnes = pd.DataFrame({
        'Frequência': frequencia_cnes,
        'Percentual (%)': percentual_cnes
    }).reset_index()

    tabela_frequencias_cnes.rename(columns={'index': 'CNES'}, inplace=True)

    # Garantir que ambos os CNES sejam do mesmo tipo
    tabela_frequencias_cnes['CNES'] = tabela_frequencias_cnes['CNES'].astype(str)
    tb_cnes['CNES'] = tb_cnes['CNES'].astype(str)

    tabela_frequencias_cnes = tabela_frequencias_cnes.merge(
        tb_cnes[['CNES', 'HOSPITAL']],
        on='CNES',
        how='left'
    )

    # Reordenar colunas para melhor visualização
    tabela_frequencias_cnes = tabela_frequencias_cnes[['CNES', 'HOSPITAL', 'Frequência', 'Percentual (%)']]

    tabela_frequencias_cnes.to_excel(output, index=False)
    return tabela_frequencias_cnes

def calcularFrequenciaMunicipios(df, output="output/freq_MUNICIPIOS.xlsx"):
    frequencia_munic_res = df["MUNIC_RES"].value_counts()
    percentual_munic_res = df["MUNIC_RES"].value_counts(normalize=True) * 100

    # Criar o DataFrame com as frequências e percentuais
    tabela_frequencias_municipios = pd.DataFrame({
        'Frequência': frequencia_munic_res,
        'Percentual (%)': percentual_munic_res
    }).reset_index()

    tabela_frequencias_municipios.rename(columns={'index': 'MUNIC_RES'}, inplace=True)

    # Garantir que ambos os MUNIC_RES sejam do mesmo tipo
    tabela_frequencias_municipios['MUNIC_RES'] = tabela_frequencias_municipios['MUNIC_RES'].astype(str)
    tab_municipio['MUNIC_RES'] = tab_municipio['MUNIC_RES'].astype(str)

    tabela_frequencias_municipios = tabela_frequencias_municipios.merge(
        tab_municipio[['MUNIC_RES', 'MUNICIPIO']],
        on='MUNIC_RES',
        how='left'
    )

    # Reordenar colunas para melhor visualização
    tabela_frequencias_municipios = tabela_frequencias_municipios[['MUNIC_RES', 'MUNICIPIO', 'Frequência', 'Percentual (%)']]

    tabela_frequencias_municipios.to_excel(output, index=False)
    return tabela_frequencias_municipios


In [67]:
calcularFrequenciaCNES(df_rede_geral,output="output/freq_CNES_geral.xlsx")

CNES                                           HOSPITAL  Frequência  \
0   2529149                IJF INSTITUTO DR JOSE FROTA CENTRAL        4281   
1   7047428      HOSPITAL E MATERNIDADE DRA ZILDA ARNS NEUMANN        2258   
2   6779522                        HOSPITAL REGIONAL DO CARIRI        1239   
3   7061021                HOSPITAL REGIONAL DO SERTAO CENTRAL         922   
4   3021114               SANTA CASA DE MISERICORDIA DE SOBRAL         509   
5   2480646                                             IMTAVI         505   
6   2415496                              HOSPITAL SAO RAIMUNDO         496   
7   2481073                                 HOSPITAL SAO LUCAS         425   
8   2564211    HOSPITAL MATERNIDADE SAO VICENTE DE PAULO HMSVP         334   
9   2328046                   HOSPITAL DR ALBERTO FEITOSA LIMA         144   
10  2529319                 PSA PRONTO SOCORRO DOS ACIDENTADOS         128   
11  2516683  HOSPITAL DISTRITAL EVANDRO AYRES DE MOURA ANTO...          90   
12  2328380                   HOSPITAL REGIONAL DR PONTES NETO          75   
13  2328003                 HOSPITAL E CASA DE SAUDE DE RUSSAS          54   
14  2562316                 HOSP MUN ABELARDO GADELHA DA ROCHA          32   
15  9672427                HOSPITAL REGIONAL VALE DO JAGUARIBE          28   
16  2552086          HOSPITAL MATERNIDADE SAO VICENTE DE PAULO          27   
17  2562871                              HOSPITAL SAO RAIMUNDO          25   
18  2651394            SANTA CASA DE MISERICORDIA DE FORTALEZA          25   
19  2611309  HOSPITAL REGIONAL DE ICO DEPUTADO ORIEL GUIMAR...          20   
20  2516640  HOSPITAL DISTRITAL MARIA JOSE BARROSO DE OLIVE...          18   
21  2415461                              HOSPITAL SANTE CARIRI          18   
22  2561492             HOSPITAL UNIVERSITARIO WALTER CANTIDIO          17   
23  2497654                    HGF HOSPITAL GERAL DE FORTALEZA          16   
24  2675536                 HOSPITAL MATERNIDADE AGENOR ARAUJO          16   
25  2527707                              HOSPITAL SAO RAIMUNDO          14   
26  2328402         HOSPITAL MUNICIPAL DR EUDASIO BARROSO HMEB          13   
27  2561433              HOSPITAL E MAT VENANCIO RAIM DE SOUSA          11   
28  2372150                                              ABEMP          11   
29  2427125                   HOSP GERAL LUIZA ALCANTARA SILVA          11   
30  2527413      HOSPITAL E MATERNIDADE REGIONAL SAO FRANCISCO          10   
31  2560976   HOSPITAL MATERNIDADE NOSSA SENHORA DA EXPECTACAO          10   
32  2560828          HOSPITAL MUNICIPAL E MATERNIDADE SAO JOSE           9   
33  2529556                 HOSP MUNIC DR DEOCLECIO LIMA VERDE           7   
34  2479710         HOSPITAL E MATERNIDADE JOSE GRANJA RIBEIRO           7   
35  2374064       HOSPITAL MUNICIPAL GOVERNADOR ADAUTO BEZERRA           7   
36  2560984                   HOSPITAL MUNICIPAL JAIME OSTERNO           5   
37  2664666                         HOSP MATERN PAULO SARASATE           5   
38  2372517                 HOSPITAL MUNICIPAL DE CAMPOS SALES           5   
39  2560852                HOSPITAL MATERNIDADE MADALENA NUNES           4   
40  2675560                        HOSPITAL REGIONAL DE IGUATU           4   
41  2561328    HOSPITAL MUNICIPAL FRANCISCA BELARMINO DA COSTA           4   
42  2372819               HOSPITAL MUNICIPAL MONSENHOR DOURADO           3   
43  2724308   HOSPITAL E MATERNIDADE ESTER CAVALCANTE ASSUNCAO           3   
44  2479818                  HOSP MATERN MENINO JESUS DE PRAGA           3   
45  2327961   HOSPITAL E MATERNIDADE ADOLFO BEZERRA DE MENEZES           3   
46  7043597                       HOSPITAL MUNICIPAL DE CARIRE           3   
47  2561336  HOSPITAL MUNICIPAL MARIA WANDERLENE NEGREIROS ...           3   
48  2561395                   HOSP GERAL MANUEL ASSUNCAO PIRES           3   
49  2806215       HOSPITAL MUNICIPAL DR JOAO ELISIO DE HOLANDA           3   
50  2479427                  

In [68]:
calcularFrequenciaMunicipios(df_rede_geral,output="output/freq_MUNICIPIO_geral.xlsx")

MUNIC_RES              MUNICIPIO  Frequência  Percentual (%)
0      230440          FORTALEZA, CE        4586       38.524866
1      230730  JUAZEIRO DO NORTE, CE         796        6.686828
2      231290             SOBRAL, CE         307        2.578965
3      230370            CAUCAIA, CE         271        2.276546
4      230765          MARACANAU, CE         237        1.990927
..        ...                    ...         ...             ...
226    351500     EMBU DAS ARTES, SP           1        0.008401
227    220800              PICOS, PI           1        0.008401
228    110020        PORTO VELHO, RO           1        0.008401
229    410580            COLOMBO, PR           1        0.008401
230    430770             ESTEIO, RS           1        0.008401

[231 rows x 4 columns]

In [69]:
grafo_rede_geral = gf.criar_grafo(geo_data, df_rede_geral)
gf.plotar_grafo_folium(grafo_rede_geral,output_path='./output/grafo_rede_geral.html')

### Rede Cirúrgica

In [70]:
grafo_rede_cirurgia = gf.criar_grafo(geo_data, df_rede_cirurgia)
gf.plotar_grafo_folium(grafo_rede_cirurgia,output_path='./output/grafo_rede_cirurgia.html')

In [56]:
calcularFrequenciaMunicipios(df_rede_cirurgia,output="output/freq_MUNICIPIO_cirurgia.xlsx")

MUNIC_RES                   MUNICIPIO  Frequência  Percentual (%)
0      230440               FORTALEZA, CE        4396       39.546599
1      230730       JUAZEIRO DO NORTE, CE         775        6.971932
2      231290                  SOBRAL, CE         292        2.626844
3      230370                 CAUCAIA, CE         261        2.347967
4      230765               MARACANAU, CE         229        2.060094
..        ...                         ...         ...             ...
224    220970  SAO FRANCISCO DO PIAUI, PI           1        0.008996
225    250370              CAJAZEIRAS, PB           1        0.008996
226    330320               NILOPOLIS, RJ           1        0.008996
227    260530                     EXU, PE           1        0.008996
228    430770                  ESTEIO, RS           1        0.008996

[229 rows x 4 columns]

In [57]:
calcularFrequenciaCNES(df_rede_cirurgia,output="output/freq_CNES_cirurgia.xlsx")

CNES                                           HOSPITAL  Frequência  \
0   2529149                IJF INSTITUTO DR JOSE FROTA CENTRAL        4111   
1   7047428      HOSPITAL E MATERNIDADE DRA ZILDA ARNS NEUMANN        2212   
2   6779522                        HOSPITAL REGIONAL DO CARIRI        1203   
3   7061021                HOSPITAL REGIONAL DO SERTAO CENTRAL         917   
4   2415496                              HOSPITAL SAO RAIMUNDO         492   
5   3021114               SANTA CASA DE MISERICORDIA DE SOBRAL         480   
6   2480646                                             IMTAVI         457   
7   2481073                                 HOSPITAL SAO LUCAS         423   
8   2564211    HOSPITAL MATERNIDADE SAO VICENTE DE PAULO HMSVP         316   
9   2529319                 PSA PRONTO SOCORRO DOS ACIDENTADOS         128   
10  2516683  HOSPITAL DISTRITAL EVANDRO AYRES DE MOURA ANTO...          90   
11  2328003                 HOSPITAL E CASA DE SAUDE DE RUSSAS          53   
12  2328046                   HOSPITAL DR ALBERTO FEITOSA LIMA          38   
13  9672427                HOSPITAL REGIONAL VALE DO JAGUARIBE          26   
14  2562316                 HOSP MUN ABELARDO GADELHA DA ROCHA          25   
15  2651394            SANTA CASA DE MISERICORDIA DE FORTALEZA          25   
16  2415461                              HOSPITAL SANTE CARIRI          18   
17  2561492             HOSPITAL UNIVERSITARIO WALTER CANTIDIO          16   
18  2675536                 HOSPITAL MATERNIDADE AGENOR ARAUJO          16   
19  2497654                    HGF HOSPITAL GERAL DE FORTALEZA          15   
20  2328380                   HOSPITAL REGIONAL DR PONTES NETO          13   
21  2372150                                              ABEMP          11   
22  2552086          HOSPITAL MATERNIDADE SAO VICENTE DE PAULO          10   
23  2529556                 HOSP MUNIC DR DEOCLECIO LIMA VERDE           7   
24  2527413      HOSPITAL E MATERNIDADE REGIONAL SAO FRANCISCO           5   
25  2328011  HOSPITAL E MATERNIDADE DIVINA PROVIDENCIA DE R...           1   
26  5018110  HOSPITAL MUNICIPAL DR JOSE EVANGELISTA DE OLIV...           1   
27  2562154                    HOSP MATERN JOAO FERREIRA GOMES           1   
28  2327945                    HOSPITAL DEPUTADO MURILO AGUIAR           1   
29  2415488      HOSPITAL E MATERNIDADE SAO FRANCISCO DE ASSIS           1   
30  2723220                           HOSPITAL HAROLDO JUACABA           1   
31  2675560                        HOSPITAL REGIONAL DE IGUATU           1   
32  2554798             HOSP MUNICIPAL DR ARGEU BRAGA HERBSTER           1   
33  2560852                HOSPITAL MATERNIDADE MADALENA NUNES           1   

    Percentual (%)  
0        36.982728  
1        19.899244  
2        10.822238  
3         8.249370  
4         4.426053  
5         4.318100  
6         4.111191  
7         3.805326  
8         2.842749  
9         1.151493  
10        0.809644  
11        0.476790  
12        0.341850  
13        0.233897  
14        0.224901  
15        0.224901  
16        0.161929  
17        0.143937  
18        0.143937  
19        0.134941  
20        0.116949  
21        0.098956  
22        0.089960  
23        0.062972  
24        0.044980  
25        0.008996  
26        0.008996  
27        0.008996  
28        0.008996  
29        0.008996  
30        0.008996  
31        0.008996  
32        0.008996  
33        0.008996